In [5]:
import pandas as pd
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
from sklearn.cluster import DBSCAN
from sklearn.preprocessing import StandardScaler
%reload_ext autoreload
%autoreload 1
%aimport utils

# og_data = pd.read_csv('data.csv')
og_data = pd.read_csv('data_engineered.csv', parse_dates=['game_date'])


In [6]:
#feature engineering
#data parsing
og_data.seconds_remaining = pd.to_timedelta(og_data.seconds_remaining, unit='s')
og_data.minutes_remaining = pd.to_timedelta(og_data.minutes_remaining, unit='m')
og_data['time_remaining'] = og_data.minutes_remaining+og_data.seconds_remaining

#binning of time_remaining
time_remaining_bins_labels = [[
    pd.Timedelta(minutes = 0),
    pd.Timedelta(minutes = 5),
    pd.Timedelta(minutes = 10),
    pd.Timedelta(minutes = 20)
], ['0-5min', '5-10min', '10-20min']]

og_data['time_remaining_label'] = pd.cut(og_data['time_remaining'], time_remaining_bins_labels[0], labels = time_remaining_bins_labels[1])
og_data['time_remaining_label2']=og_data['time_remaining_label'].astype('category').cat.codes

#use only if data needs to be regenerated
# utils.engineer_features_and_write_file(og_data)

#there are 5000 shot_made_flag null values, that's our test data, the rest is training data
test = og_data.loc[og_data['shot_made_flag'].isnull()]
data = og_data.loc[og_data['shot_made_flag'].notnull()]

og_data.describe()

chosen_features = ['shot_distance', 'period', 'home_game', 'shot_zone_area2', 'playoffs', 'time_remaining_label2', 'efficiency_normalized', 'action_type2', 'combined_shot_type2', 'opponent2']

game_event_id       game_id           lat         loc_x         loc_y  \
count   30697.000000  3.069700e+04  30697.000000  30697.000000  30697.000000   
mean      249.190800  2.476407e+07     33.953192      7.110499     91.107535   
std       150.003712  7.755175e+06      0.087791    110.124578     87.791361   
min         2.000000  2.000001e+07     33.253300   -250.000000    -44.000000   
25%       110.000000  2.050008e+07     33.884300    -68.000000      4.000000   
50%       253.000000  2.090035e+07     33.970300      0.000000     74.000000   
75%       368.000000  2.960047e+07     34.040300     95.000000    160.000000   
max       659.000000  4.990009e+07     34.088300    248.000000    791.000000   

                lon          minutes_remaining        period      playoffs  \
count  30697.000000                      30697  30697.000000  30697.000000   
mean    -118.262690  0 days 00:04:53.137440140      2.519432      0.146562   
std        0.110125  0 days 00:03:26.993848667      1.153665      0.353674   
min     -118.519800            0 days 00:00:00      1.000000      0.000000   
25%     -118.337800            0 days 00:02:00      1.000000      0.000000   
50%     -118.269800            0 days 00:05:00      3.000000      0.000000   
75%     -118.174800            0 days 00:08:00      3.000000      0.000000   
max     -118.021800            0 days 00:11:00      7.000000      1.000000   

               seconds_remaining  ...  efficiency_normalized  action_type2  \
count                      30697  ...           30697.000000  30697.000000   
mean   0 days 00:00:28.365084535  ...               0.108389     26.853601   
std    0 days 00:00:17.478949230  ...               0.137041      9.591048   
min              0 days 00:00:00  ...               0.000000      0.000000   
25%              0 days 00:00:13  ...               0.000000     26.000000   
50%              0 days 00:00:28  ...               0.064516     26.000000   
75%              0 days 00:00:43  ...               0.161290     26.000000   
max              0 days 00:00:59  ...               1.000000     56.000000   

       combined_shot_type2     opponent2     home_game  shot_zone_area2  \
count         30697.000000  30697.000000  30697.000000     30697.000000   
mean              3.086914     16.868912      0.487214         2.438023   
std               0.638599      9.062967      0.499845         1.532001   
min               0.000000      0.000000      0.000000         0.000000   
25%               3.000000      9.000000      0.000000         1.000000   
50%               3.000000     16.000000      0.000000         2.000000   
75%               3.000000     25.000000      1.000000         4.000000   
max               5.000000     32.000000      1.000000         5.000000   

              angle      distance             time_remaining  \
count  25515.000000  30697.000000                      30697   
mean       4.028277    138.476605  0 days 00:05:21.502524676   
std       52.244455     94.919782  0 days 00:03:28.175175675   
min      -90.000000      0.000000            0 days 00:00:00   
25%      -44.395313     53.338541            0 days 00:02:22   
50%        3.301866    154.350251            0 days 00:05:04   
75%       50.931527    211.243935            0 days 00:08:18   
max       90.000000    791.818792            0 days 00:11:54   

       time_remaining_label2  
count           30697.000000  
mean                0.617161  
std                 0.726174  
min                -1.000000  
25%                 0.000000  
50%                 1.000000  
75%                 1.000000  
max                 2.000000  

[8 rows x 25 columns]

In [7]:
# utils.draw_exploratory_data_charts(data, test, chosen_features)

In [8]:
## Perform DBSCAN clustering
X = data[['loc_x', 'loc_y']]
X = StandardScaler().fit_transform(X)
db = DBSCAN(eps=0.07, min_samples=50).fit(X)
labels = db.labels_
data["cluster"] = labels

In [9]:
plt.figure(figsize=(12,11))
# plt.scatter(data.loc_x, data.loc_y, c=np.where((data['shot_made_flag'] == 1), 'g', 'r'))
plt.scatter(data.loc_x, data.loc_y, c=data.cluster)
utils.draw_court()
# Adjust plot limits to just fit in half court
plt.xlim(-250,250)
# Descending values along th y axis from bottom to top
# in order to place the hoop by the top of plot
plt.ylim(422.5, -47.5)
# get rid of axis tick labels
# plt.tick_params(labelbottom=False, labelleft=False)
plt.show();

In [10]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import TimeSeriesSplit, GridSearchCV
from sklearn.ensemble import AdaBoostClassifier
from sklearn.metrics import precision_score, make_scorer

use_adaboost = True
n_jobs = 3

final_classifier = None
param_grid = None

X = data[chosen_features]
y = data['shot_made_flag']

rfc = RandomForestClassifier(max_features= 'auto', 
                             n_estimators=200,
                             oob_score = True)

print('use_adaboost: ' + str(use_adaboost))

if use_adaboost:
    final_classifier = AdaBoostClassifier(base_estimator = rfc)
    param_grid = {'base_estimator__criterion' : ['gini', 'entropy'],
              'n_estimators': [25, 100]
             } 
			 
else:
    final_classifier = rfc
    param_grid = { 'n_estimators': [25, 100],
    'max_features': ['auto', 'sqrt', 'log2']
}

tscv = TimeSeriesSplit(n_splits=2)
gsearch = GridSearchCV(estimator=final_classifier,
                       cv=tscv,
                       param_grid=param_grid,
                       scoring=make_scorer(precision_score),
                       verbose=3, 
                       n_jobs=n_jobs)
gsearch.fit(X, y)
print(gsearch.best_params_)
print(gsearch.cv_results_)

NameError: name 'chosen_features' is not defined